In [35]:
%matplotlib inline
# Importing standard Qiskit libraries and configuring account
from qiskit import QuantumCircuit, execute, Aer, IBMQ
from qiskit import QuantumRegister, ClassicalRegister
from qiskit.compiler import transpile, assemble
from qiskit.tools.jupyter import *
from qiskit.visualization import *
from qiskit.circuit import Parameter
from qiskit.result import Result

import qiskit.ignis.verification.tomography as tom
from qiskit.providers.ibmq.managed import IBMQJobManager
from qiskit.providers.jobstatus import JOB_FINAL_STATES
from qiskit.quantum_info import state_fidelity
from qiskit.providers.aer import noise

# Importing other packages
import pickle
import numpy as np

# Import measurement calibration functions
from qiskit.ignis.mitigation.measurement import (complete_meas_cal, tensored_meas_cal,
                                                 CompleteMeasFitter, TensoredMeasFitter)
from itertools import product

# Loading your IBM Q account(s)
provider = IBMQ.load_account()

ibmqfactory.load_account:WARNING:2020-05-06 20:23:41,689: Credentials are already in use. The existing account in the session will be replaced.


In [2]:
%qiskit_job_watcher

Accordion(children=(VBox(layout=Layout(max_width='710px', min_width='710px')),), layout=Layout(max_height='500…

<IPython.core.display.Javascript object>

In [3]:
%qiskit_progress_bar
from qiskit.tools.parallel import parallel_map
parallel_map(np.sin, np.linspace(0,10,100));

In [4]:
from copy import deepcopy

In [5]:
#print('\n'.join([str(x) for x in provider.backends()]))
#print('---')
#print('\n'.join([str(x) for x in Aer.backends()]))
backend=provider.get_backend('ibmq_16_melbourne')
backend_sim=provider.get_backend('ibmq_qasm_simulator')
backend_sim_local=Aer.get_backend('qasm_simulator')
backend_sv=Aer.get_backend('statevector_simulator')

In [6]:
data_list=[0,1,2,3,4]
syn=[5]
flag=[6]

In [7]:
def StatePreparation(stabilizer=0):
    q = QuantumRegister(7)
    qc = QuantumCircuit(q)
    #prepare the 5-qubit graph state
    qc.h(q[0])
    qc.h(q[1])
    qc.h(q[2])
    qc.h(q[3])
    qc.h(q[4])
    qc.cz(q[0],q[1])
    qc.cz(q[2],q[3])
    qc.cz(q[1],q[2])
    qc.cz(q[3],q[4])
    qc.cz(q[0],q[4])
    #syndrome and flag extraction
    #stabilizer order: from left to right, Fig 2(a), SM of two extra qubits
    if(stabilizer==0):
        #first stabilizer 
        qc.h(q[5])
        qc.cx(q[5],q[0])
        qc.cx(q[5],q[6])
        qc.cz(q[1],q[5])
        qc.cx(q[5],q[6])
        qc.cz(q[4],q[5])
        qc.h(q[5])
    elif(stabilizer==1):
    #second stabilizer
        qc.h(q[5])
        qc.cz(q[0],q[5])
        qc.cx(q[5],q[6])
        qc.cx(q[5],q[1])
        qc.cx(q[5],q[6])
        qc.cz(q[2],q[5])
        qc.h(q[5])
    elif(stabilizer==2):
        #third stabilizer
        qc.h(q[5])
        qc.cx(q[5],q[3])
        qc.cx(q[5],q[6])
        qc.cz(q[2],q[5])
        qc.cx(q[5],q[6])
        qc.cz(q[4],q[5])
        qc.h(q[5])
    #measure syndrome and flag & do state tomography for the data qubits
    qc.barrier()
    #qc.measure(q[5],c[5])
    #qc.measure(q[6],c[6])
    return q, qc

In [8]:
q, qc=StatePreparation(0)
# ca = ClassicalRegister(1)
# qc.add_register(ca)
# qc.measure(q[0],ca[0])
qc.draw()
# qc.data

┌───┐         ┌───┐                      ░ 
q0_0: ┤ H ├─■─────■─┤ X ├──────────────────────░─
      ├───┤ │     │ └─┬─┘                      ░ 
q0_1: ┤ H ├─■──■──┼───┼────────■───────────────░─
      ├───┤    │  │   │        │               ░ 
q0_2: ┤ H ├─■──■──┼───┼────────┼───────────────░─
      ├───┤ │     │   │        │               ░ 
q0_3: ┤ H ├─■──■──┼───┼────────┼───────────────░─
      ├───┤    │  │   │        │               ░ 
q0_4: ┤ H ├────■──■───┼────────┼───────■───────░─
      ├───┤           │        │       │ ┌───┐ ░ 
q0_5: ┤ H ├───────────■────■───■───■───■─┤ H ├─░─
      └───┘              ┌─┴─┐   ┌─┴─┐   └───┘ ░ 
q0_6: ───────────────────┤ X ├───┤ X ├─────────░─
                         └───┘   └───┘         ░

To keep the consistence, the following blocks are mainly from `test state prep.ipynb`

In [9]:
import time

Based on https://github.com/Qiskit/qiskit-tutorials/blob/master/legacy_tutorials/ignis/6a_state_tomography.ipynb?fbclid=IwAR1Pf1nH2CBPUWDdsa_xBiYs1kYDu8hwI9dVvr63z7ypmhy2UlR6QpMgJWc, 2-Qubit Conditional State Tomography

we should have projected the ideal final state to the final state, 'reduced(v,sf)' returns the projected states based on 'sf'. At the moment, for the simulation result, 'sf' can only be '00' and the func returns the first 32 elements of v.

In [10]:
def reduced(v, sf):
    s=int(sf[0])
    f=int(sf[1])
    out=s*2+f
    res=[]
    for i in range(v.shape[0]):
        if((i>>5)==out):#((i%4)==out):#
            res.append(v[i])
    res=np.array(res)
    res=res/np.sqrt(np.sum(np.power(np.abs(res),2)))
    return np.array(res)

In [11]:
def msmtErrorMitFilter(backend, measured_qubit_list):
    # backend is the backend from which we obtain measurement error rates
    #measured_qubit_list contains
    qr = QuantumRegister(len(measured_qubit_list))
    qubit_list = range(len(measured_qubit_list))
    
    # Create the measurement calibration circuits
    meas_calibs, state_labels = complete_meas_cal(qubit_list=qubit_list, qr=qr, circlabel='mcal')
    
    # Create a noise model with the qubits being measured
    noise_model = noise.NoiseModel()
    back_prop = backend.properties()
    for qi in range(len(measured_qubit_list)):
        m0_p1 = back_prop.qubit_property(qi,name='prob_meas0_prep1')[0]
        m1_p0 = back_prop.qubit_property(qi,name='prob_meas1_prep0')[0]
        read_err = noise.errors.readout_error.ReadoutError([[1-m1_p0, m1_p0],[m0_p1,1-m0_p1]])
        noise_model.add_readout_error(read_err, [qi])
    
    # Execute the calibration circuits
    job = execute(meas_calibs, backend=backend_sim_local, shots=1000, noise_model=noise_model)
    cal_results = job.result()
    
    # Calculate the calibration matrix with the noise model
    meas_fitter = CompleteMeasFitter(cal_results, state_labels, qubit_list=qubit_list, circlabel='mcal')

    # Get the filter object
    meas_filter = meas_fitter.filter
    
    return meas_filter

In [106]:
def msmtErrorMitOnTom(results, meas_filter):
    
#     print(results)
    mitigated_results = deepcopy(results)
    
    for data_idx, _ in enumerate(results.results):
        old_counts = results.get_counts(data_idx)
        new_counts = {}
        
        
#         print(old_counts)
        # removes key structure
        for reg_key in old_counts:
#             print(type(reg_key))
            reg_bits = reg_key.split(' ')
            reg_bits = reg_bits[0]+reg_bits[1]
            new_counts[reg_bits]=old_counts[reg_key]
                        
        # applies measurement filter
#         print(new_counts)
        new_counts1 = meas_filter.apply(new_counts)
#         print(new_counts1)
        
#         #replaces key structure
#         new_counts2 = {}
#         for reg_key in new_counts1:
# #             print(type(reg_key))
#             reg_bits = []
#             reg_bits.append(reg_key[0:2])
#             reg_bits.append(reg_key[2:7])
#             reg = reg_bits[0] + " " + reg_bits[1]
#             new_counts2[reg]=new_counts1[reg_key]
#         print(new_counts2)
    
        mitigated_results.results[data_idx].data.counts = \
            mitigated_results.results[data_idx]. \
            data.counts.from_dict(new_counts1)

#         new_result.results[resultidx].data.counts = \
#                     new_result.results[resultidx]. \
#                     data.counts.from_dict(new_counts)
        
#     print(mitigated_results)
    return mitigated_results

In [107]:
def sort_list(list1, list2): 
    # sorts list 1 based on the sort indices of list 2
    zipped_pairs = zip(list2, list1) 
    z = [x for _, x in sorted(zipped_pairs)] 
      
    return z 

In [108]:
def extractMsmtQubits(circuit):

    # 'circuit' is the circuit for which we extract the list of measurement qubits
    # This is some messy code. Not sure if we necessarily have to parse the qasm file of a circuit to find the qubits being measured
    # Doesn't work too well when there are two classical registers. I've written up a fix but not happy with it.
    qasm_obj = circuit.qasm()
    t = qasm_obj.find("measure")
    qasm_obj = qasm_obj[t:-1]
    qasm_obj = qasm_obj.split(' ')
    listmsmt = []
    listclass = []
    for _ in qasm_obj:
        if 'q' in _:
            number = []
            for j in range(len(_)):
                if _[j] =='[':
                    temp1 = _[j+1:j+3].strip(']')
            listmsmt.append(int(temp1))
    for _ in qasm_obj:
        if 'c' in _:
            number = []
            for j in range(len(_)):
                if _[j] =='[':
                    temp1 = _[j+1:j+3].strip(']')
            if temp1 == '0' and len(listclass) > 4:
                temp1 = '5'
            if temp1 == '1' and len(listclass) > 4:
                temp1 = '6'
            listclass.append(int(temp1))
    listmsmt = sort_list(listmsmt, listclass)
#     print(listmsmt)
#     print(listclass)
    return listmsmt

## Main part

Circuit | Description 
---| ---
qc0 | As shown in [6], state prepartion + stabilizer, no measurement
qc1 | add measurements on syndrome and flag qubits
qctom | add measurements on syndrome and flag qubits, then do state tomography on data qubits, used for tomography by both simulation and experiment
qctom_no_anc | qctom without measurement, used for 'tom.stateTomographyFitter'


In [100]:
def executeStatePreparation(stabilizer=0):
    #state vector
    q0, qc0=StatePreparation(stabilizer)
    qc0.draw()
    
    qc1=deepcopy(qc0)
    ca1 = ClassicalRegister(2)
    qc1.add_register(ca1)
    qc1.measure([q0[5],q0[6]],[ca1[0],ca1[1]])
    job = execute(qc1, backend_sv)
    psi_qc = job.result().get_statevector(qc1)
    
    #qasm simulation
    qctom = tom.state_tomography_circuits(qc0, data_list, meas_labels='Pauli', meas_basis='Pauli')
    qctom_no_anc = deepcopy(qctom)
    for qc in qctom:
        ca = ClassicalRegister(2)
        qc.add_register(ca)
        qc.measure([q0[5],q0[6]],[ca[0],ca[1]])
        
    # Create a noise model with the qubits being measured ------
    # ------used for testing measurement error mitigation on the simulator
    noise_model = noise.NoiseModel()
    back_prop = backend.properties()
    measured_qubit_list = extractMsmtQubits(qctom[-1])
    for qi in range(len(measured_qubit_list)):
        m0_p1 = back_prop.qubit_property(qi,name='prob_meas0_prep1')[0]
        m1_p0 = back_prop.qubit_property(qi,name='prob_meas1_prep0')[0]
        read_err = noise.errors.readout_error.ReadoutError([[1-m1_p0, m1_p0],[m0_p1,1-m0_p1]])
#         read_err = noise.errors.readout_error.ReadoutError([[0.7,0.3],[0.2,0.8]])
        noise_model.add_readout_error(read_err, [qi])
    
    job = execute(qctom, backend=backend_sim, optimization_level=0, shots=4096, noise_model=noise_model)
    results_sim=job.result()
    print(results_sim)
    

    # Create an error mitigation filter ------
    # ------used for testing measurement error mitigation on the simulator
    measured_qubit_list = extractMsmtQubits(qctom[-1]) # assuming all the tomo circuits are identical except for basis changes
#     print(measured_qubit_list)
    filt = msmtErrorMitFilter(backend, measured_qubit_list)
    # Perform error mitigation on all the results
    results_sim_MM = msmtErrorMitOnTom(results_sim, filt)
    results_sim = results_sim_MM
    print(results_sim)
    
#     strip the registers for syndrome and flag extraction
    result_sf={}
    for sf in ['00','01','10','11']:
            #outcomes: 00,01,10,11
            new_result = deepcopy(results_sim)

            for resultidx, _ in enumerate(results_sim.results):
                old_counts = results_sim.get_counts(resultidx)
                new_counts = {}

                #change the size of the classical register
                new_result.results[resultidx].header.creg_sizes = [new_result.results[resultidx].header.creg_sizes[0]]
                new_result.results[resultidx].header.clbit_labels = new_result.results[resultidx].header.clbit_labels[0:-2]
                new_result.results[resultidx].header.memory_slots = 5

                for reg_key in old_counts:
#                     reg_bits = []
#                     reg_bits.append(reg_key[0:2])
#                     reg_bits.append(reg_key[2:7])
#                     if (reg_bits[0]==sf):#reg_key is in the form like '00 10011', reg_bts[0]='00'
#                         new_counts[reg_bits[1]]=old_counts[reg_key]
#                     print(type(reg_key))
                    reg_bits = reg_key.split()
                    if (reg_bits[0]==sf):#reg_key is in the form like '00 10011', reg_bts[0]='00'
                        new_counts[reg_bits[1]]=old_counts[reg_key]

                new_result.results[resultidx].data.counts = \
                    new_result.results[resultidx]. \
                    data.counts.from_dict(new_counts)

                result_sf[sf]=new_result
    
    #test ----- cannot deepcopy results objects which have had some properties changed, as in above code
#     result_sf_dummy = deepcopy(result_sf['00'])
    
    #send the results to the state tomography filter
    
    tomo_qc_sim={}
#     for sf in ['00','01','10','11']:
#         tomo_qc_sim_sf = tom.StateTomographyFitter(result_sf[sf], qctom_no_anc, meas_basis='Pauli')
#         tomo_qc_sim[sf]=tomo_qc_sim_sf
    
#     max_job_count = 5
#     max_exp_per_job = 54
    
#     """ already created
#     qctom = tom.state_tomography_circuits(qc0, data_list, meas_labels='Pauli', meas_basis='Pauli')
#     for qc in qctom:
#         ca = ClassicalRegister(2)
#         qc.add_register(ca)
#         qc.measure([5,6],[5,6])
#     """
#     qctom = transpile(qctom, backend=backend)
    
#     #results_real=[]
#     #tomo_qc_real=[]
    
#     job_manager = IBMQJobManager()
#     start_time = time.time()
#     #for qc in qctom:
#     job_set_foo = job_manager.run(qctom, backend=backend, name='qctom', shots=2048, max_experiments_per_job=54)
#     job_status = job_set_foo.statuses()
#     while job_status[max_job_count-1] not in JOB_FINAL_STATES:
#         print(f'Status @ {time.time()-start_time:0.0f} s: {job_status[max_job_count-1]},'
#               f' ')
#         time.sleep(10)
#         job_status = job_set_foo.statuses()

#     results_real = job_set_foo.results()   
    
#     # Create an error mitigation filter
#     measured_qubit_list = extractMsmtQubits(qctom[-1]) # assuming all the tomo circuits are identical except for basis changes
#     filt = msmtErrorMitFilter(backend, measured_qubit_list)
#     # Perform error mitigation on all the results
#     results_real_MM = msmtErrorMitOnTom(results_real, filt)
    
#     tomo_qc_real = tom.StateTomographyFitter(results_real_MM, qctom, meas_basis='Pauli')
    #results_real.append(results_0)
    #tomo_qc_real.append(tomo_qc)
    results_real_MM = tomo_qc_real = []
    job_set_foo = 0
    return (psi_qc, results_sim, result_sf, tomo_qc_sim, job_set_foo, results_real_MM, tomo_qc_real)

In [101]:
dict={}
for i in range(1):
    data = executeStatePreparation(i)
    dict[i]=data
    #pickle.dump(data, open("Stabilizer%d"%i, "wb"))


Result(backend_name='ibmq_qasm_simulator', backend_version='0.4.1', date=datetime.datetime(2020, 5, 7, 4, 5, 3, 759966), header=Obj(backend_name='ibmq_qasm_simulator', backend_version='0.1.547'), job_id='5eb388c8df5eb7001100c51d', metadata={'max_memory_mb': 257936, 'omp_enabled': True, 'parallel_experiments': 1, 'time_taken': 5.879938924}, qobj_id='f2246121-798a-420b-b046-b200177e8869', results=[ExperimentResult(data=ExperimentResultData(counts=Obj(0x0=70, 0x1=240, 0x10=214, 0x11=50, 0x12=63, 0x13=220, 0x14=64, 0x15=223, 0x16=220, 0x17=17, 0x18=45, 0x19=189, 0x1a=185, 0x1b=13, 0x1c=195, 0x1d=25, 0x1e=23, 0x1f=153, 0x2=231, 0x20=1, 0x21=10, 0x22=6, 0x23=1, 0x24=5, 0x25=3, 0x26=1, 0x27=1, 0x28=4, 0x2b=5, 0x2c=1, 0x2d=2, 0x2e=5, 0x3=45, 0x30=7, 0x32=2, 0x33=2, 0x34=1, 0x35=4, 0x36=3, 0x37=1, 0x38=2, 0x39=4, 0x3a=5, 0x3b=1, 0x3c=3, 0x3f=4, 0x4=225, 0x41=6, 0x42=3, 0x44=3, 0x46=1, 0x47=1, 0x48=5, 0x49=2, 0x4a=1, 0x4b=2, 0x4d=1, 0x4e=2, 0x5=59, 0x50=4, 0x51=2, 0x52=2, 0x55=5, 0x56=2, 0x57=1,

{'01 01000': 4, '00 10000': 214, '01 00000': 1, '10 01110': 2, '00 10110': 220, '00 01011': 184, '00 11101': 25, '01 01011': 5, '10 10000': 4, '01 00110': 1, '00 01001': 33, '00 00010': 231, '01 10011': 2, '01 00010': 6, '10 01011': 2, '01 00100': 5, '10 11010': 4, '00 10011': 220, '00 11001': 189, '00 10100': 64, '00 00101': 59, '01 10111': 1, '10 11011': 1, '10 10111': 1, '01 00101': 3, '00 11011': 13, '10 10110': 2, '10 00100': 3, '00 10101': 223, '01 10110': 3, '01 10101': 4, '10 00001': 6, '10 10010': 2, '01 11010': 5, '01 00111': 1, '00 11100': 195, '00 11010': 185, '10 01010': 1, '01 00001': 10, '01 01101': 2, '10 11111': 1, '10 10001': 2, '01 11001': 4, '10 01101': 1, '00 10010': 63, '01 01110': 5, '11 01110': 1, '00 00100': 225, '10 11000': 1, '00 01101': 190, '00 01010': 46, '01 01100': 1, '01 10100': 1, '01 11100': 3, '10 01001': 2, '01 11000': 2, '00 01111': 19, '00 10111': 17, '00 10001': 50, '10 00110': 1, '00 01000': 221, '01 11011': 1, '01 10010': 2, '10 11001': 4, '00 

{'0000000': 120.52748266370558, '0000001': 136.06221658683867, '0000010': 114.99832895099806, '0000011': 126.6995483309136, '0000100': 127.30823427771533, '0000101': 131.7566364927884, '0000110': 133.45155982215792, '0000111': 98.33130051063931, '0001000': 144.938297950019, '0001001': 132.08242034481043, '0001010': 120.67807772600682, '0001011': 145.60853244623723, '0001100': 119.95039093749861, '0001101': 120.16033156881869, '0001110': 120.18869300713388, '0001111': 141.11295261705348, '0010000': 125.38001952818813, '0010001': 139.9013015833132, '0010010': 132.9140476088185, '0010011': 119.48168495128704, '0010100': 123.94233596638661, '0010101': 138.3317212527874, '0010110': 133.96171545520494, '0010111': 121.17915652680941, '0011000': 102.90428742785586, '0011001': 151.64085408545756, '0011010': 123.56900811702889, '0011011': 139.92532560277988, '0011100': 111.20058120781161, '0011101': 125.44588731045394, '0011110': 117.95258094122813, '0011111': 120.06373311523603, '0100000': 1.54

{'0000000': 141.4149145315492, '0000001': 101.67964230191919, '0000010': 135.03952798575196, '0000011': 125.0614046017893, '0000100': 123.2562692039361, '0000101': 141.93037875540563, '0000110': 145.93819303235787, '0000111': 147.47133557579903, '0001000': 115.75669663644541, '0001001': 117.17102386350861, '0001010': 149.52179275708195, '0001011': 120.85206036998645, '0001100': 117.53965351147232, '0001101': 115.80080274701993, '0001110': 118.19704506404516, '0001111': 108.53358355876597, '0010000': 118.50129497914645, '0010001': 105.58167100810087, '0010010': 118.575779065985, '0010011': 157.29024571570952, '0010100': 112.58822169898725, '0010101': 157.03377152114993, '0010110': 109.48638495000785, '0010111': 120.29423829263555, '0011000': 120.50005277209776, '0011001': 128.56423834760227, '0011010': 124.83301759198768, '0011011': 119.36819446137287, '0011100': 144.6761004467749, '0011101': 157.9205809757311, '0011110': 122.31795431321633, '0011111': 136.39465789312885, '0100010': 0.3

{'0000000': 109.42307668737463, '0000001': 146.3533884527028, '0000010': 170.939880624221, '0000011': 115.61601594788529, '0000100': 118.9692449095315, '0000101': 135.24260929559762, '0000110': 130.6750961059018, '0000111': 92.83490183565675, '0001000': 121.12355796603767, '0001001': 110.38349744511814, '0001010': 135.94326790170905, '0001011': 167.6863833449088, '0001100': 141.02385333471278, '0001101': 121.63471713117795, '0001110': 94.47445956690997, '0001111': 137.26356737813325, '0010000': 144.79191460872363, '0010001': 153.77789418244149, '0010010': 120.27531472049667, '0010011': 112.73449712360633, '0010100': 129.70500222933774, '0010101': 134.21839236512275, '0010110': 117.26655246455098, '0010111': 94.29846679017994, '0011000': 106.11005378780474, '0011001': 113.69802300638084, '0011010': 145.43575157741347, '0011011': 153.6307066249772, '0011100': 138.2355400134041, '0011101': 122.4467222990236, '0011110': 113.22372453262419, '0011111': 133.89231645268634, '0100000': 7.129494

...

{'0000000': 134.75222176897884, '0000001': 123.61275684409605, '0000010': 127.69987462415382, '0000011': 89.79355461163199, '0000100': 144.95385346712743, '0000101': 108.5747454645913, '0000110': 109.14130225048888, '0000111': 113.66079634850428, '0001000': 165.8494169743902, '0001001': 122.8043967700801, '0001010': 117.85663727608862, '0001011': 128.79065264549757, '0001100': 124.19705356753154, '0001101': 166.8428348195551, '0001110': 132.85819141618958, '0001111': 95.84078457589273, '0010000': 131.8444452558063, '0010001': 146.17075135082072, '0010010': 127.38702440821812, '0010011': 124.15915853449536, '0010100': 111.41540545043057, '0010101': 139.11812417053326, '0010110': 113.52550750734719, '0010111': 123.35279615282855, '0011000': 154.21678533251497, '0011001': 144.0875476048895, '0011010': 100.80867316928256, '0011011': 119.90596617416494, '0011100': 157.44085840128892, '0011101': 127.49287241203461, '0011110': 112.53594627053815, '0011111': 130.94854417129065, '0100001': 0.81

{'0000000': 252.6530897423444, '0000001': 239.97288692684316, '0000010': 242.72946973975326, '0000011': 275.13065310172817, '0000100': 2.4719355439778745, '0001000': 3.1653176038376127e-13, '0001100': 254.5681871552593, '0001101': 255.3122880863525, '0001110': 245.62599106718045, '0001111': 227.23068938949928, '0010001': 0.0446446358428563, '0010011': 3.090984216443205, '0010100': 257.1845273376203, '0010101': 271.0465651734802, '0010110': 256.7136574399412, '0010111': 256.0223002528414, '0011000': 245.4327224612914, '0011001': 251.47735206134814, '0011010': 264.2438253866042, '0011011': 253.44045615923366, '0011101': 4.123779496613752, '0011110': 1.1522852080409625, '0100000': 0.16575701102151186, '0100001': 5.055074424740543, '0100010': 6.446545128736507, '0100011': 1.0722740173530441e-13, '0100100': 1.0771824919672199e-12, '0100101': 1.0818601873727185e-12, '0101011': 1.2461309179087783e-13, '0101100': 9.222737319940916e-14, '0101101': 0.31865904903502695, '0101111': 4.6840771769923

{'0000000': 238.1108183771406, '0000001': 9.838928799285608, '0000010': 275.88004297917576, '0000100': 4.818489449800198, '0000101': 285.52937762884847, '0000110': 6.845175511112036, '0000111': 252.5974655965422, '0001000': 2.5686526913999436e-12, '0001001': 250.134543341037, '0001011': 271.0567083526371, '0001100': 258.9954496340418, '0001110': 246.43112281675957, '0010001': 217.47211219661722, '0010011': 241.35525148845193, '0010100': 276.3823750321079, '0010101': 11.682282888833896, '0010110': 239.15019697101678, '0010111': 11.590671722326887, '0011000': 240.2309736722173, '0011001': 8.668090871068027e-12, '0011010': 250.71526214294497, '0011011': 3.947707622359601e-12, '0011101': 261.37941863681533, '0011111': 238.03339426458643, '0100000': 1.167886724872336, '0100001': 1.3834594904269188e-12, '0100010': 0.5931374699296689, '0100110': 1.0379607262122996e-12, '0100111': 3.37419353660948e-12, '0101001': 6.69900046994579e-12, '0101010': 2.5997312704412754e-12, '0101011': 1.15011998459

{'0000000': 241.5170303154542, '0000001': 4.401333365271522, '0000010': 253.06782386420463, '0000011': 11.932605225454815, '0000100': 256.29953927904364, '0000101': 2.3292627366330128, '0000110': 292.9447334847589, '0000111': 3.118260595279276e-11, '0001000': 9.007628693580367, '0001001': 223.06548920857705, '0001011': 219.1071748219364, '0001100': 2.5148399862399713e-11, '0001101': 252.0160452213552, '0001110': 6.098753348109218e-11, '0001111': 271.0669134992411, '0010001': 251.43042267252133, '0010010': 7.155385094861715e-11, '0010011': 315.9252671264699, '0010100': 7.18544742816748e-11, '0010101': 248.789708388665, '0010110': 3.934661050993807, '0010111': 244.55535191218078, '0011000': 231.77760574627683, '0011001': 0.4378949619657282, '0011010': 271.0614854720282, '0011011': 2.1560631667478852e-11, '0011100': 250.3865801830074, '0011110': 238.51685015547196, '0100100': 4.7725494075386704e-12, '0100101': 4.456223747211635e-12, '0100111': 6.921652046822362e-12, '0101000': 1.269067865

{'0000000': 126.33196055342994, '0000001': 129.724707638393, '0000010': 113.89730683626281, '0000011': 129.2519794010197, '0000100': 138.84250027337995, '0000101': 111.0738549860519, '0000110': 129.4045583651936, '0000111': 145.11498407738594, '0001000': 136.09613837645534, '0001001': 119.37792613461436, '0001010': 120.91356138377928, '0001011': 117.30326397288344, '0001100': 132.4274255152699, '0001101': 140.3627763845592, '0001110': 126.15727857917642, '0001111': 132.73349337402934, '0010000': 147.08578624930504, '0010001': 109.77723317588219, '0010010': 124.23866973289422, '0010011': 136.22884349586488, '0010100': 115.39413094271201, '0010101': 124.73541360510413, '0010110': 135.54698643897748, '0010111': 132.57784305111082, '0011000': 107.75918574335132, '0011001': 116.48919082299315, '0011010': 118.22244861330952, '0011011': 141.98572139090354, '0011100': 132.18544611542555, '0011101': 120.58106399191071, '0011110': 147.5411496187931, '0011111': 103.6416548749669, '0100000': 1.809

### Analyze the first stabilizer's result

In [102]:
psi_qc0, results_sim0, result_sf0, tomo_qc_sim0, job_set_foo0, results_real0, tomo_qc_real0=dict[0]

In [105]:
# print(results_sim0.to_dict())
# print(result_sf0)
dummy = result_sf0['00'].dict()
# dummy = results_sim0.to_dict()
dimmy = deepcopy(dummy)

for idx, _ in enumerate(dimmy['results']):
    if (idx == 0):
        temp = _['data']['counts'] 
        print(temp)
#         print(type(temp))
        newcs = {}
        for idxx, j in enumerate(temp):
            print(type(j))
            k = str(hex(int(j,2)))
            newcs[k] = temp[j]
        _['data']['counts'] = newcs
        temp = _['data']['counts'] 
        print(temp)
print(dimmy)
res = Result.from_dict(dimmy)
# print(dimmy)
print(res)

{'0111010': 1.28229462980482e-12, '0100001': 4.206981564903849, '1010011': 2.553180706965399e-11, '0110110': 6.148322607781273e-13, '0001011': 244.1426789359314, '0011111': 217.85322362784106, '0100000': 1.5876238703698552e-11, '1000000': 1.655769446736303e-11, '0011100': 258.52353777711653, '1000110': 5.253763766267456e-12, '1000101': 1.7737533553069892e-12, '1110110': 1.174956661527179e-12, '0010011': 279.5670563129508, '1110100': 2.5822265376368693e-13, '1010110': 1.6903082615336717e-11, '1010100': 8.5014509316801e-12, '0110001': 1.0370631284808469e-11, '0111101': 7.523297494560635e-12, '0010101': 279.7549125798886, '0001101': 245.37263741988042, '0010111': 8.371876118307769e-11, '0011010': 245.60981580856114, '1000111': 1.0299752284440466e-11, '0111100': 2.0285597867977835e-11, '0101001': 5.6920719402032564e-12, '1100000': 1.1656154869325305e-12, '1001101': 1.1036509884338718e-11, '0011101': 9.469704987608183e-12, '0000011': 7.541051797530093e-11, '0001001': 4.8614913113569274e-11,

ModelValidationError: "{'results': {1: {'data': {'counts': [{'0100001': ['String does not match expected pattern.'], '1010011': ['String does not match expected pattern.'], '0001011': ['String does not match expected pattern.'], '0011111': ['String does not match expected pattern.'], '1100101': ['String does not match expected pattern.'], '1000010': ['String does not match expected pattern.'], '1111101': ['String does not match expected pattern.'], '0011100': ['String does not match expected pattern.'], '1101001': ['String does not match expected pattern.'], '1000101': ['String does not match expected pattern.'], '0010011': ['String does not match expected pattern.'], '1110100': ['String does not match expected pattern.'], '1010100': ['String does not match expected pattern.'], '0110001': ['String does not match expected pattern.'], '1001010': ['String does not match expected pattern.'], '0111101': ['String does not match expected pattern.'], '0010101': ['String does not match expected

In [42]:
qcc, qc0=StatePreparation(0)
qc0.draw()
qc1=deepcopy(qc0)
ca1 = ClassicalRegister(2)
qc1.add_register(ca1)
qc1.measure([qcc[5],qcc[6]],[ca1[0],ca1[1]])
job0 = execute(qc1, backend_sv)

In [43]:
qctom = tom.state_tomography_circuits(qc0, data_list, meas_labels='Pauli', meas_basis='Pauli')
qctom_no_anc = deepcopy(qctom)

for qc in qctom:
    ca = ClassicalRegister(2)
    qc.add_register(ca)
    qc.measure([qcc[5],qcc[6]],[ca[0],ca[1]])

In [ ]:
qctom1 = tom.state_tomography_circuits(qc0, [0,1,2,3,4,5,6], meas_labels='Pauli', meas_basis='Pauli')

In [44]:
qctom[-1].draw()

┌───┐         ┌───┐                      ░  ░ ┌─┐                  
   q7_0: ┤ H ├─■─────■─┤ X ├──────────────────────░──░─┤M├──────────────────
         ├───┤ │     │ └─┬─┘                      ░  ░ └╥┘┌─┐               
   q7_1: ┤ H ├─■──■──┼───┼────────■───────────────░──░──╫─┤M├───────────────
         ├───┤    │  │   │        │               ░  ░  ║ └╥┘┌─┐            
   q7_2: ┤ H ├─■──■──┼───┼────────┼───────────────░──░──╫──╫─┤M├────────────
         ├───┤ │     │   │        │               ░  ░  ║  ║ └╥┘┌─┐         
   q7_3: ┤ H ├─■──■──┼───┼────────┼───────────────░──░──╫──╫──╫─┤M├─────────
         ├───┤    │  │   │        │               ░  ░  ║  ║  ║ └╥┘┌─┐      
   q7_4: ┤ H ├────■──■───┼────────┼───────■───────░──░──╫──╫──╫──╫─┤M├──────
         ├───┤           │        │       │ ┌───┐ ░  ░  ║  ║  ║  ║ └╥┘┌─┐   
   q7_5: ┤ H ├───────────■────■───■───■───■─┤ H ├─░──░──╫──╫──╫──╫──╫─┤M├───
         └───┘              ┌─┴─┐   ┌─┴─┐   └───┘ ░  ░  ║  ║  ║  ║  ║ └╥┘┌─┐
   q7_6: ───────────────────┤ X ├───┤ X ├─────────░──░──╫──╫──╫──╫──╫──╫─┤M├
                            └───┘   └───┘         ░  ░  ║  ║  ║  ║  ║  ║ └╥┘
c1227_0: ═══════════════════════════════════════════════╩══╬══╬══╬══╬══╬══╬═
                                                           ║  ║  ║  ║  ║  ║ 
c1227_1: ══════════════════════════════════════════════════╩══╬══╬══╬══╬══╬═
                                                              ║  ║  ║  ║  ║ 
c1227_2: ═════════════════════════════════════════════════════╩══╬══╬══╬══╬═
                                                                 ║  ║  ║  ║ 
c1227_3: ════════════════════════════════════════════════════════╩══╬══╬══╬═
                                                                    ║  ║  ║ 
c1227_4: ═══════════════════════════════════════════════════════════╩══╬══╬═
                                                                       ║  ║ 
c1470_0: ══════════════════════════════════════════════════════════════╩══╬═
                                                                          ║ 
c1470_1: ═════════════════════════════════════════════════════════════════╩═

In [45]:
job = execute(qctom, backend=backend_sim, optimization_level=0, shots=4096)
results_sim=job.result()
print(results_sim)


Result(backend_name='ibmq_qasm_simulator', backend_version='0.4.1', date=datetime.datetime(2020, 5, 7, 3, 30, 1, 94198), header=Obj(backend_name='ibmq_qasm_simulator', backend_version='0.1.547'), job_id='5eb380ac69fc280011cc4e6e', metadata={'max_memory_mb': 257936, 'omp_enabled': True, 'parallel_experiments': 1, 'time_taken': 3.931323664}, qobj_id='8c3a60ae-fc8c-4aa8-a74e-cf12981b788d', results=[ExperimentResult(data=ExperimentResultData(counts=Obj(0x1=244, 0x10=268, 0x13=250, 0x15=262, 0x16=253, 0x19=275, 0x1a=243, 0x1c=250, 0x1f=252, 0x2=258, 0x4=258, 0x7=267, 0x8=255, 0xb=237, 0xd=274, 0xe=250)), header=Obj(clbit_labels=[['c1227', 0], ['c1227', 1], ['c1227', 2], ['c1227', 3], ['c1227', 4], ['c1228', 0], ['c1228', 1]], creg_sizes=[['c1227', 5], ['c1228', 2]], memory_slots=7, n_qubits=7, name="('X', 'X', 'X', 'X', 'X')", qreg_sizes=[['q7', 7]], qubit_labels=[['q7', 0], ['q7', 1], ['q7', 2], ['q7', 3], ['q7', 4], ['q7', 5], ['q7', 6]]), meas_level=<MeasLevel.CLASSIFIED: 2>, metadata={'

In [48]:
# TESTING

# Create an error mitigation filter ------
# ------used for testing measurement error mitigation on the simulator
measured_qubit_list = extractMsmtQubits(qctom[-1]) # assuming all the tomo circuits are identical except for basis changes
print(measured_qubit_list)
filt = msmtErrorMitFilter(backend, measured_qubit_list)
# Perform error mitigation on all the results
results_sim_MM = msmtErrorMitOnTom(results_sim, filt)
print(results_sim_MM)

[0, 1, 2, 3, 4, 5, 6]
{'00 00100': 258, '00 01101': 274, '00 10000': 268, '00 10110': 253, '00 01011': 237, '00 10101': 262, '00 01110': 250, '00 01000': 255, '00 11100': 250, '00 00001': 244, '00 11010': 243, '00 00010': 258, '00 11111': 252, '00 10011': 250, '00 11001': 275, '00 00111': 267}
{'0000100': 258, '0001101': 274, '0010000': 268, '0010110': 253, '0001011': 237, '0010101': 262, '0001110': 250, '0001000': 255, '0011100': 250, '0000001': 244, '0011010': 243, '0000010': 258, '0011111': 252, '0010011': 250, '0011001': 275, '0000111': 267}
{'0000000': 5.31761651963924e-14, '0000001': 225.4050810626695, '0000010': 238.59506261082794, '0000011': 3.160555077430494e-14, '0000100': 237.23162616801042, '0000101': 4.173760899851014e-14, '0000110': 3.375640246770188e-14, '0000111': 271.85193409185155, '0001000': 241.22109465643138, '0001001': 2.5978313547452105e-14, '0001010': 2.8320716511698977e-14, '0001011': 248.2955254108076, '0001100': 2.77120826433949e-14, '0001101': 290.1451214436

NameError: name 'new_counts2' is not defined

In [ ]:
job_tmp=job_set_foo0.jobs()[0]

In [ ]:
jobs_tmp=job_set_foo0.jobs()[0]

In [ ]:
numresult=0
for i in range(len(job_set_foo0.jobs())):
    numresult+=len(job_set_foo0.jobs()[i].result().get_counts())
print(numresult)

In [ ]:
result_tmp=result_sf0['00']

### Strip the registers of syndrome and flag in results obtained from real qc
only '00' is kept

In [ ]:
numjobs=len(job_set_foo0.jobs())
#sf only consider 00
new_real_results=[]
for jobidx in range(numjobs):
    #job_set_foo0.jobs()[jobidx]
    numresults=len(job_set_foo0.jobs()[jobidx].result().results)
    new_result = deepcopy(job_set_foo0.jobs()[jobidx].result())
    for resultidx in range(numresults):
        #outcomes: 00,01,10,11

        old_counts=job_set_foo0.jobs()[jobidx].result().get_counts()[resultidx]
        new_counts={}
        new_result.results[resultidx].header.creg_sizes = [new_result.results[resultidx].header.creg_sizes[0]]
        new_result.results[resultidx].header.clbit_labels = new_result.results[resultidx].header.clbit_labels[0:-2]
        new_result.results[resultidx].header.memory_slots = 5

        for reg_key in old_counts:
            reg_bits = reg_key.split(' ')
            if (reg_bits[0]=='00'):#reg_key is in the form like '00 10011', reg_bts[0]='00'
                new_counts[reg_bits[1]]=old_counts[reg_key]

        new_result.results[resultidx].data.counts = \
            new_result.results[resultidx]. \
            data.counts.from_dict(new_counts)

    new_real_results.append(new_result)


Since there are multiple jobs, we need to combine the results with all kinds of Pauli measurements together

In [ ]:
new_real_results_sum=new_real_results[0]

In [ ]:
for i in range(len(new_real_results)-1):
    new_real_results_sum.results.extend(new_real_results[i+1].results)

Syndrome and flag are always 0 in the ideal simulation 

In [ ]:
rho_qc_sf0 = tomo_qc_sim0['11'].fit(method='lstsq')
# print(results_sim0)

In [ ]:
print(results_sim0)

fidelity between the reduced statevector of the circuit without measurement, and the reconstructed state of simulation tomography results

In [ ]:
F_qc_sf0 = state_fidelity(reduced(psi_qc0,'00'), rho_qc_sf0)
print(F_qc_sf0)

The following fidelity calculations are incorrect because noisy experimental results include those with non-zero syndrome or flag.

The fidelity between reconstruction using the simulation data and reconstruction using the real qc data

In [ ]:
tomo_qc_real00=tom.StateTomographyFitter(new_real_results_sum, qctom_no_anc, meas_basis='Pauli')

Show the difference between simulation & experiment outcomes with different Pauli bases...(not very accurate)

$\sum_{Pauli} (\sum_{i=00000}^{11111} |prob(i, simulation)-prob(i, experiment)|)$

$Pauli=(XXXXX, XXXXY, ..., ZZZZZ)$


In [ ]:
sum_diff=0
for key in tomo_qc_sim0['00'].data.keys():
    sum_sim=np.sum(list(tomo_qc_sim0['00'].data[key].values()))
    sum_real=np.sum(list(tomo_qc_real00.data[key].values()))
    diff=0
    for i in range(2**5):
        diff+=np.abs((tomo_qc_sim0['00'].data[key].get(bin(i)[2:],0)/sum_sim - tomo_qc_real00.data[key].get(bin(i)[2:],0)/sum_real))
    print(key, diff)
    sum_diff+=diff
print(sum_diff)

In [ ]:
tomo_qc_real00.data.values()

In [ ]:
tomo_qc_sim0['00'].data

In [ ]:
tomo_qc_real00.data

In [ ]:
from qiskit.visualization import *

In [ ]:
plot_histogram([tomo_qc_real00.data[('Z', 'Z', 'Z', 'Z', 'Z')],tomo_qc_sim0['00'].data[('Z', 'Z', 'Z', 'Z', 'Z')]])

In [ ]:
rho_real_sf00= tomo_qc_real00.fit(method='lstsq')

In [ ]:
np.linalg.norm(rho_real_sf00)

In [ ]:
F_qc_0=state_fidelity(rho_qc_sf0, rho_real_sf00)
print(F_qc_0)

Fidelity between the real-quantum-computer-data reconstruction and the ideal statevector

In [ ]:
F_qc_1=state_fidelity(reduced(psi_qc0,'00'), rho_real_sf00)
print(F_qc_1)

In [ ]:
test_allzero=np.zeros((32,32))
test_allzero[0][0]=1
F_qc_test=state_fidelity(reduced(psi_qc0, '00'),test_allzero)
print(F_qc_test)

In [ ]:
qctom_trans = transpile(qctom, backend=backend)

In [ ]:
for qc_trans in qctom_trans:
    print(qc_trans.depth())